In [2]:
import pandas as pd
import pickle

In [3]:
with open('result_0802_without_ID_UP.txt','rb') as f:
    res = pickle.load(f)

In [6]:
def zuhe(line):
    line['hour'] = line['hour'].astype(str)
    line['weekday'] = line['weekday'].astype(str)
    line['s_ij'] = line['s_ij'].astype(str)
    line['e_ij'] = line['e_ij'].astype(str)

#     line['is_peek'] = line['is_peek'].astype(str)
    line['is_crowd'] = line['is_crowd'].astype(str)
                                   
    line['hour_weekday'] = line['hour'] + line['weekday']
    line['hour_crowd'] = line['hour'] + line['is_crowd']
    line['hour_s'] = line['hour'] + line['s_ij']
    line['hour_e'] = line['hour'] + line['e_ij']

    line['hour'] = line['hour'].astype(int)
#     line['is_peek'] = line['is_peek'].astype(int)
    line['is_crowd'] = line['is_crowd'].astype(int)
    line['weekday'] = line['weekday'].astype(int)
    line['s_ij'] = line['s_ij'].astype(int)
    line['e_ij'] = line['e_ij'].astype(int)
    
    line['hour_weekday'] = line['hour_weekday'].astype(int)
    line['hour_crowd'] = line['hour_crowd'].astype(int)
    line['hour_s'] = line['hour_s'].astype(int)
    line['hour_e'] = line['hour_e'].astype(int)
    return line

In [7]:
with open('./data/test-id4-crowd-grid3.txt', 'rb') as data_file:
    test = pickle.load(data_file)
test = zuhe(test)
test = test[['ID', 'new_dist',  'O_LINENO', 'O_UP', 'Source_Station', 'Target_Station',
       'Distance', 'distance2', 'O_TIME', 'hour', 'is_peek', 'weekday',
       'is_workday', 'dws', 'nws', 'dts', 'nts', 'is_rain', 'max_v',
       'h_aver_diff', 'h_aver_d', 'h_aver_v', 'TERMINALNO', 
       'is_crowd', 's_ij', 'e_ij','grid_aver_diff', 'grid_aver_d', 'hour_weekday', 'hour_crowd', 'hour_s', 'hour_e']]
test.columns=['ID', 'Distance',  'O_LINENO', 'O_UP', 'Source_Station', 'Target_Station',
       'Distance1', 'distance2', 'O_TIME', 'hour', 'is_peek', 'weekday',
       'is_workday', 'dws', 'nws', 'dts', 'nts', 'is_rain', 'max_v',
       'h_aver_diff', 'h_aver_d', 'h_aver_v', 'TERMINALNO', 
       'is_crowd', 's_ij', 'e_ij','grid_aver_diff', 'grid_aver_d', 'hour_weekday', 'hour_crowd', 'hour_s', 'hour_e']
col1 = [c for c in test if
       c not in ['Unnamed: 0','ID2' , 's_x', 's_y', 'e_x', 'e_y','O_LINENO', 'O_UP', 'Source_Station', 'Target_Station', 'O_TIME', 'aver_v', 'max_v',
                 'Diff_Time','Distance1', 'distance2','TERMINALNO', 'new_dist']]
print(col1)

['ID', 'Distance', 'hour', 'is_peek', 'weekday', 'is_workday', 'dws', 'nws', 'dts', 'nts', 'is_rain', 'h_aver_diff', 'h_aver_d', 'h_aver_v', 'is_crowd', 's_ij', 'e_ij', 'grid_aver_diff', 'grid_aver_d', 'hour_weekday', 'hour_crowd', 'hour_s', 'hour_e']


In [10]:
test['pred1'] = res
test['pred2'] = res

In [12]:
sub1 = test[['O_LINENO','TERMINALNO', 'O_UP','Source_Station','Target_Station','O_TIME','pred1','pred2','Distance','Distance1']]
sub1['O_TIME'] = pd.to_datetime(sub1['O_TIME'],format='%Y-%m-%d %H:%M:%S')
sub1.columns = ['LINE','TERMINALNO','UP','pred_start_stop_ID','pred_end_stop_ID','realTime','pred1','pred2','Distance','Distance1']
sub1 = sub1.reset_index()
del sub1['index']

sub=pd.read_csv("./toBePredicted_0607_segment.csv", sep=",")
sub['realTime'] = pd.to_datetime(sub['realTime'],format='%Y-%m-%d %H:%M:%S')
sub2 = sub[['LINE','TERMINALNO','UP','pred_start_stop_ID','pred_end_stop_ID','realTime','distance']]
sub2=pd.merge(sub2,sub1,on=['LINE','TERMINALNO','UP','pred_start_stop_ID','pred_end_stop_ID','realTime'],how='left')

/home/kawayi-4/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [14]:
sub2['div_dist'] = sub2['Distance'] / sub2['Distance1']
sub2['new_pred'] = sub2['div_dist'] * sub2['pred1']

import math
for i in range(sub2.shape[0]):
    s = sub2.iloc[i]
    if math.isnan(s['div_dist']):
        sub2.loc[i,'new_pred'] = s['pred1']
        
sub2.to_csv('./toBePredicted_0802_result.csv',sep=",",index=False)#0605 29.2467

print('finished')

finished


In [15]:
print((sub2['pred1']-sub2['pred2']).mean())
print((sub2['pred2']-sub2['new_pred']).mean())
print((sub2['pred1']-sub2['new_pred']).mean())

0.0
4.073720933263226
4.073720933263226


In [16]:
sub2['new_pred'].mean()

119.71784697515088

In [25]:
!python answer.py

answer.py:21: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  y_pred = myresult['new_pred'].as_matrix()#np.random.random_integers(low=120,high=140,size=len(myresult))#
0 27.954292762638815;186.8567130181085;258.71175829948754;355.8655573865432;599.6555251806835;737.4600678136771;812.1099358311039;930.4066693665541;1117.5379784273932;1259.967711181518;1405.546220245064;1654.5728394624348;1816.967809641805;2119.1198377148576;2188.8868974854945;2425.3048480355096;2515.0209107966616;2613.3521849197764;2811.9036160941087;3100.041610104883;3175.1935104462027;3310.615635252119;
1 65.67533793023115;269.0301875777689;353.6202464886141;507.0747391842956;816.5983543523957;956.2223912573891;1048.0385244728852;1132.8736590185183;1361.5667060527578;1428.2241979164514;1543.4792681288134;1715.3834064422401;1728.3592404531948;1781.8000811632637;1894.0778786563947;1987.7737211580659;2046.793350732007;2102.695270874375;
2 10;97.93808577610375;203.7650633748264

41 76.32262903716162;223.3894661608685;344.1852739988645;494.3175079753436;600.6096381101974;734.4038425891827;827.1577539902281;887.3025963286977;950.2440564693105;1006.3434159106016;1058.772600188481;1113.8719111181802;1182.278720183306;1234.4730707557032;
42 10;133.2363047016131;217.96451292519566;328.3883475375423;477.1388263356678;654.8244545146207;737.6272989650153;
43 46.85846443736608;142.69833444298328;258.54605504228374;385.148306830294;449.43553356859593;498.9960343743876;597.7148117500784;699.0113708598575;766.6205734844804;841.6234059861235;909.1647531331869;1124.6647803137741;1178.138505313314;1258.8486782756493;1355.0077423724592;1398.1349130932722;1463.8435728800207;1534.5019546997523;1680.2681024906406;1772.0977142632846;1823.2053678453597;1991.3535539728275;2441.3535539728273;2601.5867665324486;2755.444562012451;
44 295.4342163291376;383.9281230276665;756.7165641260347;919.7988997416293;1292.5873408399973;1350.8141158121093;1426.1506254419232;1509.747056640959;1637.55

98 10;81.72926125480436;139.04464735512718;202.72308070720558;421.56461873477963;605.7648046790293;721.5845816715018;936.9772143693211;1051.8717733828619;
99 10;115.74706494115804;220.30712107582275;516.7024672547034;621.6079441051168;758.6160036964136;842.927551000554;985.4073812796014;1058.6128886063061;
100 10;247.22253536376755;385.90029165478825;486.15408964161696;616.0033344271044;770.6776235915432;900.1164872226461;
101 74.5631617380241;288.9113271891449;439.86894434460464;629.7032959313752;719.4716768808449;820.9216629958642;938.1202650435694;996.8717528699676;1091.3598762098595;1172.1823477000903;1380.6094379878202;1474.6976636484414;1543.3509225371201;1644.4815727407395;
102 178.42360407057637;440.5367110449246;594.412646939629;721.9317318544028;1136.0690142226333;1204.7571827403003;1406.143050185888;1578.5219737538007;1665.5369367791307;1766.9337694983496;2025.0692671403929;2035.0692671403929;2110.441136707165;2167.7464529843905;2284.217270202039;2394.209725428633;2470.39337

132 10;99.45099942830082;259.9426358874345;480.5763218104094;754.2668431674808;938.1665300962504;1043.8504635856145;1302.097355297619;1495.0766829179815;1631.6207614910925;
133 39.51567326679488;310.7317827808207;583.6307961544264;695.8774354277026;850.1531743979949;985.1975338970633;1146.9418185071036;1577.9954740568737;1696.7836855314276;1794.229895725773;1949.2288896381974;2094.551600170087;2267.9500944354522;2355.3268140852706;2577.8890689800946;2716.53725478089;
134 56.89216033612439;125.35176766386577;225.8552301031123;326.30169108760356;433.3810440403547;544.124064859641;642.954321657952;901.6642455547793;1035.68374708338;1157.1913407386578;1232.908128401923;1354.2790734965204;1503.4490107483261;1614.2092858245744;1748.4083789171711;1822.9291683920655;1891.5837537612667;1928.8278511550143;2007.5241070819332;2075.461719795601;2157.883694992204;2295.3738684544305;2426.889544629155;2523.538689005164;2719.0174177386666;2766.192648506833;3041.8876749196957;
135 88.00676855133031;206.

166 179.23124862718083;286.7987781004622;635.3510255140145;990.6876316131668;1432.545044389964;1698.1918619756902;2120.4172950263146;2360.137780704437;2756.1574628011476;2815.4277106907466;2949.8321751241897;3121.2061925744747;3325.5628960941176;3494.647447351508;
167 29.648295535223557;64.59866952119859;116.99973721507784;171.22026434431868;210.96873806141627;276.6771389067317;370.4571632610631;412.40480667406246;474.44553101010064;550.6843861559025;646.4067487512922;752.737469062474;786.4162190811164;904.1737506213431;1080.719117583334;1141.5152026682326;1190.0447435934857;1322.4177029683078;1384.2866398160193;1433.553542125206;1597.8460955796913;1661.7181375196085;1729.4682732928918;1843.8299906563645;1947.8988115256102;2096.484800835156;2171.242940643553;2268.74075264349;2460.922173258998;2579.9727006346125;2700.2816188165757;2920.3638854521178;2994.2088278641104;3050.8496462940943;3117.928651383193;3251.5058975115203;3329.133393450049;3499.9999999999995;
168 87.3258507071724;231.3

...

30448 10;177.77310638608273;263.0311352453885;330.96342672178986;421.96041903957956;522.0484096604547;616.997224450279;691.8294177949097;890.2200007756187;1340.2200007756187;1597.4229666924684;1766.0428975274751;1867.5770101338392;1952.7139558925105;2007.5389403720612;2096.680556899247;2240.087940881254;2422.338762860848;
30449 52.82061929492234;216.36169711423673;369.65101769311923;472.4319331122524;622.2962047079445;671.4626222653645;856.4371328733564;971.8276042374272;1194.3946905834882;
30450 281.00140643152736;413.2056849624339;536.7150841232868;681.9705024118621;757.8036387861729;
30451 257.42571869821404;331.8237950570109;438.95334230288825;569.3285421539367;657.853477661968;743.159974164652;803.2470636592112;905.2688445552026;1019.9953766878721;1107.7767468405502;1202.9223181028847;1321.004369874767;1417.4600317892523;1469.2016020569783;1513.332603808929;
30452 10;101.88397870142865;161.99302569790447;252.22665708439217;402.937805160058;549.4084170545592;880.805261125643;964.60

30494 52.372597600535975;113.10639826042805;226.6900287832519;317.1373541945864;400.64766952147903;554.8526528378895;682.6761137507888;
30495 10;99.35261343465305;160.66637845454062;215.94414104711873;328.6422294341024;445.27520951887834;556.1056406195489;646.8359976857536;704.9520432898707;1042.6619974103578;1099.036918430998;1160.84745139165;1232.590659552652;1372.4365245965316;1483.5903085437603;1527.6250484529107;1570.0633206347375;1710.8197711771888;1781.235872018733;1870.3485983402254;1996.079435811298;
30496 55.0647767560107;148.22250960377954;258.7578183441276;390.0520812768791;483.75720780322587;609.255059659546;733.3321625711329;882.12471436511;936.2707046334116;1141.5899286840338;1273.6934997552612;1407.0668155846577;1469.207043199338;1545.9736003952082;1618.5686411522775;1831.9664543080473;
30497 22.435913455527995;83.80781109123261;185.2330925901377;325.3811498394817;497.865789208518;610.4460019918513;718.1587573095982;836.1693914152693;
30498 114.98365246352603;207.507499

30539 131.9915493919774;282.03427064802133;617.385344898953;826.042932720639;991.598821370214;1248.061115619065;1484.8415429323504;1653.245899973319;1785.1620313259532;1845.8903029499002;1906.380728386654;2004.9753251317604;2157.431415080306;2276.8739919717523;2395.200115098969;2467.9612465885216;
30540 63.9422744474825;242.4677037787388;383.7538652668867;494.24604344186787;578.1715577397661;720.5930810295911;810.7361255103189;1119.8532939312338;
30541 10;162.65353586448455;275.4412326392802;351.84620611646915;453.17881251591865;548.7648987881103;816.6440990705499;889.8897766179174;996.7068262987336;
30542 113.62387811275482;323.04607781582513;421.4792208975725;570.4845913913225;632.708828712702;819.6515223207454;870.5733894225967;956.8442316193594;1045.4516522995416;1185.6626110016914;1258.129872513148;
30543 47.64110347329347;145.61607071427085;223.01768117648504;279.2343588815098;340.35141932630165;412.84428824609404;525.003964072547;587.4624264943757;649.0518742031595;792.305241699

30585 84.60637014680532;217.13984349454566;294.66312468722845;339.21618292278407;467.98766888246496;607.4713129648187;999.7296578003459;1159.3397946554403;1258.6488897519666;1380.7724260984292;1598.0461777188139;1666.898333804975;1729.234204195669;1846.6319949248802;2061.250982363328;2145.0418189361762;2386.7129335644017;2490.6460394883284;2602.7471683893527;
30586 99.8219706932848;146.360907808342;268.1305986444815;410.704934615179;502.52592750612143;661.5185889894514;747.3822733288013;803.0643545486832;917.8495566585979;1009.5370969651348;1186.8901549435473;1265.463047241915;1357.0889241273912;1435.616558884031;1526.4610415865548;1606.9232084035953;1663.7930974304509;1726.494992201121;1858.2330370924053;1926.8728951355772;2000.7068150049545;2195.775384026052;
30587 82.12372936495936;154.86668821130849;194.01336858439433;350.3236920855245;453.5337370845153;532.4703001964456;718.277998064846;853.8184148577457;1000.0772501926883;1166.9053002221058;1303.4878016924;1531.753044662862;1609.

30631 33.074910579875166;145.86775125364508;252.016104073238;355.4371181347508;596.3231284977013;801.943072723057;866.388192886281;997.0246989968375;1249.0245470167201;1599.723193210574;1828.982890200967;1988.596627240298;2097.6862035994577;2368.9157980070845;2774.311110137177;
30632 129.87489846149776;289.5320228067094;479.04246658442827;621.0217534223627;676.548447995398;741.6930790061272;874.1187090664524;1105.7465279997293;1230.1917293376614;1439.7517383496513;1707.356976883269;1854.7237940607254;1929.9722582814334;2139.912328676539;2342.7243282595136;
30633 84.60916718091215;229.70190818491074;376.31748339106537;499.99341088591393;566.5280263815393;677.1161506416571;743.6997219503271;843.9269717960026;973.2236861235995;1127.434103080725;1236.3987069964774;1356.7998441654229;1573.9293552528218;1836.4029501128578;2025.5536956839596;2168.3079515440804;2439.5963863126212;2564.5597851425255;2651.384435636069;2760.755810324361;2869.4411935122453;3200.8155249401407;3310.9967875071366;346